In [213]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
from sklearn.model_selection import train_test_split
from torch.utils.data import Dataset, DataLoader
from sklearn.preprocessing import LabelEncoder, StandardScaler, MinMaxScaler

In [226]:
from datasets import load_dataset

dataset = load_dataset("scikit-learn/churn-prediction", split="train").to_csv("churn.csv")

Creating CSV from Arrow format: 100%|██████████| 8/8 [00:00<00:00, 261.01ba/s]


Customer churn prediction dataset of a fictional telecommunication company made by IBM Sample Datasets. Context Predict behavior to retain customers. You can analyze all relevant customer data and develop focused customer retention programs.

Content Each row represents a customer, each column contains customer’s attributes described on the column metadata.

The data set includes information about:

Customers who left within the last month: the column is called Churn
Services that each customer has signed up for: phone, multiple lines, internet, online security, online backup, device protection, tech support, and streaming TV and movies
Customer account information: how long they’ve been a customer, contract, payment method, paperless billing, monthly charges, and total charges
Demographic info about customers: gender, age range, and if they have partners and dependents

In [262]:
data = pd.read_csv("churn.csv")
labels_data = data["Churn"]
data.drop(columns=["customerID", "Churn"], inplace=True)
data

gender  SeniorCitizen Partner Dependents  tenure PhoneService  \
0     Female              0     Yes         No       1           No   
1       Male              0      No         No      34          Yes   
2       Male              0      No         No       2          Yes   
3       Male              0      No         No      45           No   
4     Female              0      No         No       2          Yes   
...      ...            ...     ...        ...     ...          ...   
7038    Male              0     Yes        Yes      24          Yes   
7039  Female              0     Yes        Yes      72          Yes   
7040  Female              0     Yes        Yes      11           No   
7041    Male              1     Yes         No       4          Yes   
7042    Male              0      No         No      66          Yes   

         MultipleLines InternetService OnlineSecurity OnlineBackup  \
0     No phone service             DSL             No          Yes   
1                   No             DSL            Yes           No   
2                   No             DSL            Yes          Yes   
3     No phone service             DSL            Yes           No   
4                   No     Fiber optic             No           No   
...                ...             ...            ...          ...   
7038               Yes             DSL            Yes           No   
7039               Yes     Fiber optic             No          Yes   
7040  No phone service             DSL            Yes           No   
7041               Yes     Fiber optic             No           No   
7042                No     Fiber optic            Yes           No   

     DeviceProtection TechSupport StreamingTV StreamingMovies        Contract  \
0                  No          No          No              No  Month-to-month   
1                 Yes          No          No              No        One year   
2                  No          No          No              No  Month-to-month   
3                 Yes         Yes          No              No        One year   
4                  No          No          No              No  Month-to-month   
...               ...         ...         ...             ...             ...   
7038              Yes         Yes         Yes             Yes        One year   
7039              Yes          No         Yes             Yes        One year   
7040               No          No          No              No  Month-to-month   
7041               No          No          No              No  Month-to-month   
7042              Yes         Yes         Yes             Yes        Two year   

     PaperlessBilling              PaymentMethod  MonthlyCharges TotalCharges  
0                 Yes           Electronic check           29.85        29.85  
1                  No               Mailed check           56.95       1889.5  
2                 Yes               Mailed check           53.85       108.15  
3                  No  Bank transfer (automatic)           42.30      1840.75  
4                 Yes           Electronic check           70.70       151.65  
...               ...                        ...             ...          ...  
7038              Yes               Mailed check           84.80       1990.5  
7039              Yes    Credit card (automatic)          103.20       7362.9  
7040              Yes           Electronic check           29.60       346.45  
7041              Yes               Mailed check           74.40        306.6  
7042              Yes  Bank transfer (automatic)          105.65       6844.5  

[7043 rows x 19 columns]

In [263]:
labels_data

0        No
1        No
2       Yes
3        No
4       Yes
       ... 
7038     No
7039     No
7040     No
7041    Yes
7042     No
Name: Churn, Length: 7043, dtype: object

In [281]:
columns = [
    'gender',
    'SeniorCitizen',
    'Partner',
    'Dependents',
    'tenure',
    'PhoneService',
    'MultipleLines',
    'InternetService',
    'OnlineSecurity',
    'OnlineBackup',
    'DeviceProtection',
    'TechSupport',
    'StreamingTV',
    'StreamingMovies',
    'Contract',
    'PaperlessBilling',
    'PaymentMethod'
]

scaler = MinMaxScaler()

for col in columns:
    print(col)
    data[col] = LabelEncoder().fit_transform(data[col])


gender
SeniorCitizen
Partner
Dependents
tenure
PhoneService
MultipleLines
InternetService
OnlineSecurity
OnlineBackup
DeviceProtection
TechSupport
StreamingTV
StreamingMovies
Contract
PaperlessBilling
PaymentMethod


In [282]:
data

gender  SeniorCitizen  Partner  Dependents  tenure  PhoneService  \
0          0              0        1           0       1             0   
1          1              0        0           0      34             1   
2          1              0        0           0       2             1   
3          1              0        0           0      45             0   
4          0              0        0           0       2             1   
...      ...            ...      ...         ...     ...           ...   
7038       1              0        1           1      24             1   
7039       0              0        1           1      72             1   
7040       0              0        1           1      11             0   
7041       1              1        1           0       4             1   
7042       1              0        0           0      66             1   

      MultipleLines  InternetService  OnlineSecurity  OnlineBackup  \
0                 1                0               0             2   
1                 0                0               2             0   
2                 0                0               2             2   
3                 1                0               2             0   
4                 0                1               0             0   
...             ...              ...             ...           ...   
7038              2                0               2             0   
7039              2                1               0             2   
7040              1                0               2             0   
7041              2                1               0             0   
7042              0                1               2             0   

      DeviceProtection  TechSupport  StreamingTV  StreamingMovies  Contract  \
0                    0            0            0                0         0   
1                    2            0            0                0         1   
2                    0            0            0                0         0   
3                    2            2            0                0         1   
4                    0            0            0                0         0   
...                ...          ...          ...              ...       ...   
7038                 2            2            2                2         1   
7039                 2            0            2                2         1   
7040                 0            0            0                0         0   
7041                 0            0            0                0         0   
7042                 2            2            2                2         2   

      PaperlessBilling  PaymentMethod  MonthlyCharges TotalCharges  
0                    1              2           29.85        29.85  
1                    0              3           56.95       1889.5  
2                    1              3           53.85       108.15  
3                    0              0           42.30      1840.75  
4                    1              2           70.70       151.65  
...                ...            ...             ...          ...  
7038                 1              3           84.80       1990.5  
7039                 1              1          103.20       7362.9  
7040                 1              2           29.60       346.45  
7041                 1              3           74.40        306.6  
7042                 1              0          105.65       6844.5  

[7043 rows x 19 columns]

In [287]:
data.to_csv("test.csv")

In [288]:
data = pd.read_csv("test.csv")

there were spaces in the data so i needed to remove those

testing if theres weird data by trying label encode on every column

In [283]:
import seaborn as sns

scaler = MinMaxScaler()
print(data["gender"])
data = scaler.fit_transform(data["gender"])

In [289]:
from torchvision.transforms import v2
transformations = v2.Compose([
   v2.ToTensor()
])

c:\Users\johns\AppData\Local\Programs\Python\Python310\lib\site-packages\torchvision\transforms\v2\_deprecated.py:41: UserWarning: The transform `ToTensor()` is deprecated and will be removed in a future release. Instead, please use `v2.Compose([v2.ToImage(), v2.ToDtype(torch.float32, scale=True)])`.
  warnings.warn(


In [291]:
transformations(data.astype(float))

Unnamed: 0  gender  SeniorCitizen  Partner  Dependents  tenure  \
0            0.0     0.0            0.0      1.0         0.0     1.0   
1            1.0     1.0            0.0      0.0         0.0    34.0   
2            2.0     1.0            0.0      0.0         0.0     2.0   
3            3.0     1.0            0.0      0.0         0.0    45.0   
4            4.0     0.0            0.0      0.0         0.0     2.0   
...          ...     ...            ...      ...         ...     ...   
7038      7038.0     1.0            0.0      1.0         1.0    24.0   
7039      7039.0     0.0            0.0      1.0         1.0    72.0   
7040      7040.0     0.0            0.0      1.0         1.0    11.0   
7041      7041.0     1.0            1.0      1.0         0.0     4.0   
7042      7042.0     1.0            0.0      0.0         0.0    66.0   

      PhoneService  MultipleLines  InternetService  OnlineSecurity  \
0              0.0            1.0              0.0             0.0   
1              1.0            0.0              0.0             2.0   
2              1.0            0.0              0.0             2.0   
3              0.0            1.0              0.0             2.0   
4              1.0            0.0              1.0             0.0   
...            ...            ...              ...             ...   
7038           1.0            2.0              0.0             2.0   
7039           1.0            2.0              1.0             0.0   
7040           0.0            1.0              0.0             2.0   
7041           1.0            2.0              1.0             0.0   
7042           1.0            0.0              1.0             2.0   

      OnlineBackup  DeviceProtection  TechSupport  StreamingTV  \
0              2.0               0.0          0.0          0.0   
1              0.0               2.0          0.0          0.0   
2              2.0               0.0          0.0          0.0   
3              0.0               2.0          2.0          0.0   
4              0.0               0.0          0.0          0.0   
...            ...               ...          ...          ...   
7038           0.0               2.0          2.0          2.0   
7039           2.0               2.0          0.0          2.0   
7040           0.0               0.0          0.0          0.0   
7041           0.0               0.0          0.0          0.0   
7042           0.0               2.0          2.0          2.0   

      StreamingMovies  Contract  PaperlessBilling  PaymentMethod  \
0                 0.0       0.0               1.0            2.0   
1                 0.0       1.0               0.0            3.0   
2                 0.0       0.0               1.0            3.0   
3                 0.0       1.0               0.0            0.0   
4                 0.0       0.0               1.0            2.0   
...               ...       ...               ...            ...   
7038              2.0       1.0               1.0            3.0   
7039              2.0       1.0               1.0            1.0   
7040              0.0       0.0               1.0            2.0   
7041              0.0       0.0               1.0            3.0   
7042              2.0       2.0               1.0            0.0   

      MonthlyCharges  TotalCharges  
0              29.85         29.85  
1              56.95       1889.50  
2              53.85        108.15  
3              42.30       1840.75  
4              70.70        151.65  
...              ...           ...  
7038           84.80       1990.50  
7039          103.20       7362.90  
7040           29.60        346.45  
7041           74.40        306.60  
7042          105.65       6844.50  

[7043 rows x 20 columns]

## NO CLUE IF THIS WAS RIGHT BUT WOOOOOOOOHOOOOOOOOOOOOOOOOOOOOOOOOOOOO

In [294]:
X = data
y = labels_data.astype(float)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=7)

# Step 3: Creating PyTorch Dataset and DataLoader
class ChurnDataset(Dataset):
    def __init__(self, X, y):
        self.X = torch.tensor(X.values, dtype=torch.float32)
        self.y = torch.tensor(y.values, dtype=torch.float32)
        
    def __len__(self):
        return len(self.X)
    
    def __getitem__(self, idx):
        return self.X[idx], self.y[idx]

train_dataset = ChurnDataset(X_train, y_train)
test_dataset = ChurnDataset(X_test, y_test)

train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)

# Step 4: Define a Neural Network Model
class ChurnModel(nn.Module):
    def __init__(self):
        super().__init__()
        self.fc1 = nn.Linear(len(X.columns), 64)
        self.fc2 = nn.Linear(64, 32)
        self.fc3 = nn.Linear(32, 1)
        self.relu = nn.ReLU()
        
    def forward(self, x):
        #x = torch.relu(self.fc1(x))
        #x = torch.relu(self.fc2(x))
        #x = self.sigmoid(self.fc3(x))
        return self.fc3(self.relu((self.fc2(self.relu(self.fc1(x))))))


ValueError: could not convert string to float: 'No'

In [ ]:
# Step 5: Define Loss Function and Optimizer
model = ChurnModel()
criterion = nn.BCEWithLogitsLoss()
optimizer = optim.SGD(model.parameters(), lr=0.0001)

In [ ]:
epochs = 100

In [ ]:
print(train_dataset[0])

(tensor([ 1.0000,  0.0000,  1.0000,  1.0000,  1.6137,  1.0000,  0.0000,  2.0000,
         1.0000,  1.0000,  1.0000,  1.0000,  1.0000,  1.0000,  2.0000,  0.0000,
         0.0000, -1.4894, -0.4237]), tensor(0.))


In [ ]:

for epoch in range(epochs):

    model.train()

    running_loss = 0.0

    for inputs, labels in train_loader:
        
        outputs = model(inputs).squeeze()
        print(outputs)
        print(outputs.shape)
        outpreds = torch.round(torch.sigmoid(outputs))
        loss = criterion(outputs, labels) # somethin wrong heree
        optimizer.zero_grad(set_to_none=True)
        loss.backward()
        optimizer.step()
        running_loss += loss.item() * inputs.size(0)
    epoch_loss = running_loss / len(train_dataset)
    #print(f'Epoch [{epoch+1}/{epochs}], Loss: {epoch_loss:.4f}')

tensor([-0.1676, -0.1066, -0.1388, -0.1333, -0.1310, -0.1408, -0.1461, -0.1466,
        -0.1432, -0.1162, -0.1205, -0.1192, -0.1444, -0.1824, -0.1205, -0.1139,
        -0.1620, -0.0820, -0.1814, -0.1538, -0.1699, -0.1672, -0.1721, -0.1237,
        -0.1265, -0.0830, -0.1102, -0.1195, -0.1519, -0.1314, -0.0982, -0.1107],
       grad_fn=<SqueezeBackward0>)
torch.Size([32])
tensor([-0.0908, -0.1228, -0.1285, -0.1340, -0.2120, -0.0493, -0.1489, -0.1015,
        -0.1331, -0.0993, -0.0907, -0.1129, -0.0978, -0.0345, -0.1146, -0.1337,
        -0.1766, -0.0857, -0.1576, -0.1268, -0.1242, -0.1265, -0.1472, -0.1276,
        -0.0470, -0.1797, -0.1189, -0.1234, -0.1146, -0.0355, -0.0721, -0.1392],
       grad_fn=<SqueezeBackward0>)
torch.Size([32])
tensor([-0.1747, -0.1614, -0.1239, -0.1081, -0.1767, -0.1374, -0.1950, -0.1450,
        -0.1806, -0.0853, -0.1411, -0.1535, -0.1184, -0.1533, -0.1436, -0.1598,
        -0.1072, -0.1370, -0.1358, -0.0654, -0.1597, -0.1012, -0.1191, -0.0867,
        -0.107